<a href="https://colab.research.google.com/github/tejcancode27/DL-Assignment-2/blob/main/Q1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install tensorflow
!pip install numpy
!pip install scikit-learn
!pip install matplotlib


In [ ]:

import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Embedding, SimpleRNN, LSTM, GRU, Dense
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.model_selection import train_test_split


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
dataset_path = "/content/drive/MyDrive/dakshina_dataset_v1.0/dakshina_dataset_v1.0/bn/lexicons/bn.translit.sampled.train.tsv"

In [ ]:
english_sentences,bengali_sentences = [], []
with open(dataset_path, 'r', encoding='utf-8') as file:
    for line in file:
        eng, ben = line.strip().split('\t')[:2]
        english_sentences.append(eng)
        bengali_sentences.append('\t' + ben + '\n')  # Add start/end tokens
print(english_sentences)
print(bengali_sentences)

['অংকিত', 'অংকিত', 'অংকিত', 'অংকিত', 'অংকিত', 'অংকিত', 'অংকিত', 'অংকের', 'অংকের', 'অংকের', 'অংশ', 'অংশ', 'অংশ', 'অংশ', 'অংশ', 'অংশ', 'অংশ', 'অংশ', 'অংশই', 'অংশই', 'অংশই', 'অংশই', 'অংশও', 'অংশও', 'অংশও', 'অংশও', 'অংশকে', 'অংশকে', 'অংশকে', 'অংশকেই', 'অংশকেই', 'অংশকেই', 'অংশগুলি', 'অংশগুলি', 'অংশগুলির', 'অংশগুলির', 'অংশগুলির', 'অংশগুলো', 'অংশগুলো', 'অংশগুলো', 'অংশগুলোর', 'অংশগুলোর', 'অংশগুলোর', 'অংশগুলোর', 'অংশগুলোর', 'অংশগুলোর', 'অংশগুলোর', 'অংশগুলোর', 'অংশগ্রহণ', 'অংশগ্রহণ', 'অংশগ্রহণ', 'অংশগ্রহণ', 'অংশগ্রহণ', 'অংশগ্রহণ', 'অংশগ্রহণ', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারী', 'অংশগ্রহণকারীদের', 'অংশগ্রহণকারীদের', 'অংশগ্রহণকারীদের', 'অংশগ্রহণকারীদের', 'অংশগ্রহণকারীদের', 'অংশগ্রহণকারীদের', 'অংশগ্রহণকারীদের', 'অংশগ্রহণকে', 'অংশগ্রহণকে', 'অংশগ্রহণকে', 'অংশগ্রহণকে', 'অংশগ্রহণকে', 'অংশগ্রহণকে', 'অংশগ্রহণকে', 'অংশগ্রহণকে', 'অংশগ্রহণকে', 'অংশগ্রহণক

In [ ]:
input_alphabet = sorted(set("".join(english_sentences)))
output_alphabet = sorted(set("".join(bengali_sentences)))

input_char_to_index = {char: idx+1 for idx, char in enumerate(input_alphabet)}  # reserve 0 for padding
output_char_to_index = {char: idx+1 for idx, char in enumerate(output_alphabet)}
reverse_output_char_to_index = {idx: char for char, idx in output_char_to_index.items()}

input_vocab_size = len(input_char_to_index) + 1
output_vocab_size = len(output_char_to_index) + 1
print(input_alphabet)
print(output_alphabet)
print(input_char_to_index)
print(output_char_to_index)

['ঁ', 'ং', 'ঃ', 'অ', 'আ', 'ই', 'ঈ', 'উ', 'ঊ', 'ঋ', 'এ', 'ঐ', 'ও', 'ঔ', 'ক', 'খ', 'গ', 'ঘ', 'ঙ', 'চ', 'ছ', 'জ', 'ঝ', 'ঞ', 'ট', 'ঠ', 'ড', 'ঢ', 'ণ', 'ত', 'থ', 'দ', 'ধ', 'ন', 'প', 'ফ', 'ব', 'ভ', 'ম', 'য', 'র', 'ল', 'শ', 'ষ', 'স', 'হ', '়', 'া', 'ি', 'ী', 'ু', 'ূ', 'ৃ', 'ে', 'ৈ', 'ো', 'ৌ', '্', 'ৎ', '২']
['\t', '\n', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z']
{'ঁ': 1, 'ং': 2, 'ঃ': 3, 'অ': 4, 'আ': 5, 'ই': 6, 'ঈ': 7, 'উ': 8, 'ঊ': 9, 'ঋ': 10, 'এ': 11, 'ঐ': 12, 'ও': 13, 'ঔ': 14, 'ক': 15, 'খ': 16, 'গ': 17, 'ঘ': 18, 'ঙ': 19, 'চ': 20, 'ছ': 21, 'জ': 22, 'ঝ': 23, 'ঞ': 24, 'ট': 25, 'ঠ': 26, 'ড': 27, 'ঢ': 28, 'ণ': 29, 'ত': 30, 'থ': 31, 'দ': 32, 'ধ': 33, 'ন': 34, 'প': 35, 'ফ': 36, 'ব': 37, 'ভ': 38, 'ম': 39, 'য': 40, 'র': 41, 'ল': 42, 'শ': 43, 'ষ': 44, 'স': 45, 'হ': 46, '়': 47, 'া': 48, 'ি': 49, 'ী': 50, 'ু': 51, 'ূ': 52, 'ৃ': 53, 'ে': 54, 'ৈ': 55, 'ো': 56, 'ৌ': 57, '্': 58, 'ৎ': 59, '২': 60}
{'\t': 1, '\n': 2, 'a': 

In [ ]:
encoder_input_data = [[input_char_to_index[c] for c in seq] for seq in english_sentences]
decoder_input_data = [[output_char_to_index[c] for c in seq] for seq in bengali_sentences]
decoder_output_data = [seq[1:] for seq in decoder_input_data]

max_encoder_seq_length = max(len(seq) for seq in encoder_input_data)
max_decoder_seq_length = max(len(seq) for seq in decoder_input_data)

encoder_input_data = pad_sequences(encoder_input_data, maxlen=max_encoder_seq_length, padding='post')
decoder_input_data = pad_sequences(decoder_input_data, maxlen=max_decoder_seq_length, padding='post')
decoder_output_data = pad_sequences(decoder_output_data, maxlen=max_decoder_seq_length, padding='post')

decoder_output_data_onehot = tf.keras.utils.to_categorical(decoder_output_data, num_classes=output_vocab_size)


In [ ]:
def create_seq2seq_model(rnn_type='LSTM', embedding_size=64, hidden_size=128, num_rnn_layers=1):
    RNN = {'RNN': SimpleRNN, 'LSTM': LSTM, 'GRU': GRU}[rnn_type]

    # Encoder
    encoder_inputs = Input(shape=(None,))
    encoder_embedding = Embedding(input_vocab_size, embedding_size)(encoder_inputs)

    for i in range(num_rnn_layers):
        return_sequences = (i != num_rnn_layers - 1)
        if i == 0:
            encoder_rnn = RNN(hidden_size, return_sequences=return_sequences, return_state=True)
            if rnn_type == 'LSTM':
                _, encoder_state_h, encoder_state_c = encoder_rnn(encoder_embedding)
                encoder_states = [encoder_state_h, encoder_state_c]
            else:
                _, encoder_state_h = encoder_rnn(encoder_embedding)
                encoder_states = [encoder_state_h]
        else:
            encoder_embedding = RNN(hidden_size, return_sequences=return_sequences)(encoder_embedding)

    # Decoder
    decoder_inputs = Input(shape=(None,))
    decoder_embedding = Embedding(output_vocab_size, embedding_size)(decoder_inputs)

    for i in range(num_rnn_layers):
        return_sequences = True
        if i == 0:
            decoder_rnn = RNN(hidden_size, return_sequences=return_sequences, return_state=True)
            if rnn_type == 'LSTM':
                decoder_outputs, _, _ = decoder_rnn(decoder_embedding, initial_state=encoder_states)
            else:
                decoder_outputs, _ = decoder_rnn(decoder_embedding, initial_state=encoder_states)
        else:
            decoder_embedding = RNN(hidden_size, return_sequences=return_sequences)(decoder_embedding)

    decoder_dense = Dense(output_vocab_size, activation='softmax')
    decoder_outputs = decoder_dense(decoder_outputs)

    seq2seq_model = Model([encoder_inputs, decoder_inputs], decoder_outputs)
    return seq2seq_model

In [ ]:
seq2seq_model = create_seq2seq_model(rnn_type='LSTM', embedding_size=128, hidden_size=256, num_rnn_layers=1)
seq2seq_model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

seq2seq_model.fit(
    [encoder_input_data, decoder_input_data],
    decoder_output_data_onehot,
    batch_size=64,
    epochs=20,
    validation_split=0.2
)

Epoch 1/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 16s 10ms/step - accuracy: 0.7094 - loss: 0.9965 - val_accuracy: 0.7405 - val_loss: 1.0902
Epoch 2/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 18s 10ms/step - accuracy: 0.7931 - loss: 0.6366 - val_accuracy: 0.7764 - val_loss: 0.9949
Epoch 3/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 22s 11ms/step - accuracy: 0.8721 - loss: 0.3938 - val_accuracy: 0.8287 - val_loss: 0.7554
Epoch 4/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 19s 9ms/step - accuracy: 0.9152 - loss: 0.2538 - val_accuracy: 0.8514 - val_loss: 0.7312
Epoch 5/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 21s 10ms/step - accuracy: 0.9298 - loss: 0.2036 - val_accuracy: 0.8518 - val_loss: 0.6953
Epoch 6/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 13s 11ms/step - accuracy: 0.9358 - loss: 0.1802 - val_accuracy: 0.8605 - val_loss: 0.7237
Epoch 7/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 12s 10ms/step - accuracy: 0.9397 - loss: 0.1648 - val_accuracy: 0.8580 - val_loss: 0.6428
Epoch 8/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 20s 10ms/step - accuracy: 0.9423 - 

In [ ]:

from tensorflow import keras  # Import keras from tensorflow
# Encoder inference model
encoder_inputs = seq2seq_model.input[0]  # Input to encoder
# Get the correct LSTM layer name - it's likely 'lstm_16' based on the error message
encoder_outputs, encoder_state_h, encoder_state_c = seq2seq_model.get_layer("lstm").output  # Changed 'lstm' to 'lstm_16'
encoder_states = [encoder_state_h, encoder_state_c]
encoder_model = keras.Model(encoder_inputs, encoder_states)

latent_size = encoder_states[0].shape[-1]

decoder_inputs = seq2seq_model.input[1]  # Input to decoder
# Pass decoder inputs through embedding layer
decoder_embedding = seq2seq_model.get_layer("embedding_1")(decoder_inputs)  # This line was added

decoder_state_input_h = keras.Input(shape=(latent_size,), name="input_h")
decoder_state_input_c = keras.Input(shape=(latent_size,), name="input_c")
decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]

# Similarly, adjust the decoder LSTM layer name - likely 'lstm_17'
decoder_lstm = seq2seq_model.get_layer("lstm_1")  # Changed 'lstm_1' to 'lstm_17'
decoder_outputs, decoder_state_h, decoder_state_c = decoder_lstm(
    decoder_embedding, initial_state=decoder_states_inputs  # decoder_inputs was changed to decoder_embedding
)
decoder_states = [decoder_state_h, decoder_state_c]
decoder_dense = seq2seq_model.get_layer("dense")  # Or "dense_18" if that's the actual name from the error
decoder_outputs = decoder_dense(decoder_outputs)

decoder_inference_model = keras.Model(
    [decoder_inputs] + decoder_states_inputs,
    [decoder_outputs] + decoder_states
)


In [ ]:
def translate_sequence(input_sequence):
    # Encode the input as state vectors
    state_values = encoder_model.predict(input_sequence)

    # Generate empty target sequence with just the start character
    target_sequence = np.zeros((1, 1))
    target_sequence[0, 0] = output_char_to_index['\t']

    # Store the decoded characters
    decoded_sentence = ""

    while True:
        output_tokens, h, c = decoder_inference_model.predict([target_sequence] + state_values)

        # Sample a token
        sampled_token_idx = np.argmax(output_tokens[0, -1, :])
        sampled_char = reverse_output_char_to_index[sampled_token_idx]
        decoded_sentence += sampled_char

        # Exit condition: either hit max length or find stop character
        if (sampled_char == '\n' or len(decoded_sentence) > max_decoder_seq_length):
            break

        # Update the target sequence
        target_sequence[0, 0] = sampled_token_idx
        state_values = [h, c]

    return decoded_sentence

In [ ]:
X_train_split, X_test_split, y_train_split, y_test_split = train_test_split(
    encoder_input_data, decoder_input_data, test_size=0.1, random_state=42)

# Predict sample
for idx in range(5):
    input_sequence = X_test_split[idx:idx+1]
    decoded = translate_sequence(input_sequence)
    print("Input:", english_sentences[idx])
    print("Predicted:", decoded)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 341ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 212ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 77ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 55ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
Input: অংকিত
Predicted: cheerojiboner

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━

In [ ]:
def load_test_data(file_path):
    test_data = []
    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            line = line.strip()
            if '\t' in line:
                # Splitting the line by tabs and taking only the first two elements
                parts = line.split('\t')
                input_text, target_text = parts[:2]  # Assign the first two elements to input_text and target_text
                target_text = '\t' + target_text + '\n'  # for seq2seq start/end tokens
                test_data.append((input_text, target_text))
    return test_data

test_data = load_test_data('/content/drive/MyDrive/dakshina_dataset_v1.0/dakshina_dataset_v1.0/bn/lexicons/bn.translit.sampled.train.tsv')  # ✅ update with your correct path
test_input_texts = [inp for inp, _ in test_data]
test_target_texts = [tgt for _, tgt in test_data]

embedding_size = 64
hidden_size = 256
rnn_type = 'LSTM'
num_rnn_layers = 1

In [ ]:
!pip install tensorflow
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
tokenizer_input = Tokenizer()
tokenizer_input.fit_on_texts(english_sentences)  # Fit on training data

tokenizer_output = Tokenizer(char_level=True)  # char_level=True for decoder
tokenizer_output.fit_on_texts(bengali_sentences)

encoder_test_input_data = tokenizer_input.texts_to_sequences(test_input_texts)
encoder_test_input_data = pad_sequences(encoder_test_input_data, maxlen=max_encoder_seq_length, padding='post')

decoder_test_input_data = tokenizer_output.texts_to_sequences([t[:-1] for t in test_target_texts])
decoder_test_input_data = pad_sequences(decoder_test_input_data, maxlen=max_decoder_seq_length, padding='post')

decoder_test_target_data = tokenizer_output.texts_to_sequences([t[1:] for t in test_target_texts])
decoder_test_target_data = pad_sequences(decoder_test_target_data, maxlen=max_decoder_seq_length, padding='post')

# One-hot encode the targets
decoder_test_target_data_onehot = to_categorical(decoder_test_target_data, num_classes=output_vocab_size)

In [ ]:
seq2seq_model = create_seq2seq_model(
    rnn_type=rnn_type,
    embedding_size=embedding_size,
    hidden_size=hidden_size,
    num_rnn_layers=num_rnn_layers
)

seq2seq_model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

In [ ]:
print(f"\n🔁 Training model with embedding_size={embedding_size}, hidden_size={hidden_size}...")
seq2seq_model.fit(
    [encoder_input_data, decoder_input_data],
    decoder_output_data_onehot,
    batch_size=64,
    epochs=20,
    validation_split=0.2,
    verbose=1
)


🔁 Training model with embedding_size=64, hidden_size=256...
Epoch 1/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 12s 10ms/step - accuracy: 0.7232 - loss: 0.9022 - val_accuracy: 0.7287 - val_loss: 1.1184
Epoch 2/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 11s 10ms/step - accuracy: 0.7874 - loss: 0.6591 - val_accuracy: 0.7615 - val_loss: 1.0917
Epoch 3/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 20s 9ms/step - accuracy: 0.8563 - loss: 0.4379 - val_accuracy: 0.7998 - val_loss: 0.9637
Epoch 4/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 21s 10ms/step - accuracy: 0.9013 - loss: 0.2990 - val_accuracy: 0.8215 - val_loss: 0.8855
Epoch 5/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 22s 11ms/step - accuracy: 0.9211 - loss: 0.2353 - val_accuracy: 0.8337 - val_loss: 0.8509
Epoch 6/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 19s 10ms/step - accuracy: 0.9304 - loss: 0.2013 - val_accuracy: 0.8422 - val_loss: 0.7744
Epoch 7/20
1182/1182 ━━━━━━━━━━━━━━━━━━━━ 20s 10ms/step - accuracy: 0.9360 - loss: 0.1811 - val_accuracy: 0.8446 - val_loss: 0.7971
Epoch 8/20
1182/

In [ ]:
print("\n📊 Evaluating on test set...")
test_loss, test_accuracy = seq2seq_model.evaluate(
    [encoder_test_input_data, decoder_test_input_data],
    decoder_test_target_data_onehot,
    verbose=1
)

print(f"\n✅ Final Test Accuracy (embedding_size={embedding_size}): {test_accuracy:.4f}")


📊 Evaluating on test set...
2955/2955 ━━━━━━━━━━━━━━━━━━━━ 14s 5ms/step - accuracy: 0.6191 - loss: 3.0806

✅ Final Test Accuracy (embedding_size=64): 0.6197


In [ ]:
!git init

hint: Using 'master' as the name for the initial branch. This default branch name
hint: is subject to change. To configure the initial branch name to use in all
hint: of your new repositories, which will suppress this warning, call:
hint: 
hint: 	git config --global init.defaultBranch <name>
hint: 
hint: Names commonly chosen instead of 'master' are 'main', 'trunk' and
hint: 'development'. The just-created branch can be renamed via this command:
hint: 
hint: 	git branch -m <name>
Initialized empty Git repository in /content/.git/


In [ ]:
!git config --global user.email "saitejaswi.e04@gmail.com"

In [ ]:
!git config --global user.name "tejcancode27"

In [ ]:
!git remote add origin https://github.com/tejcancode27/DL-Assignment-2.git

In [ ]:
!echo "*.gdoc" >> .gitignore
!echo "*.gsheet" >> .gitignore
!echo "*.gslides" >> .gitignore
!echo "*.ipynb_checkpoints/" >> .gitignore
!echo "__pycache__/" >> .gitignore
!echo "*.pyc" >> .gitignore
!echo ".DS_Store" >> .gitignore


In [ ]:
!git rm --cached "drive/MyDrive/IT-3 VI SEM Placement fee details .gform"


fatal: pathspec 'drive/MyDrive/IT-3 VI SEM Placement fee details .gform' did not match any files


In [ ]:
!git add .



error: open("drive/MyDrive/IT-3 VI SEM Placement fee details .gform"): Operation not supported
error: unable to index file 'drive/MyDrive/IT-3 VI SEM Placement fee details .gform'
fatal: adding files failed


In [2]:
def create_seq2seq_model(rnn_type, embedding_dim, hidden_units, num_layers):
    from tensorflow.keras.models import Model
    from tensorflow.keras.layers import Input, Embedding, LSTM, GRU, SimpleRNN, Dense

    RNNLayer = {"LSTM": LSTM, "GRU": GRU, "SimpleRNN": SimpleRNN}[rnn_type]

    # Encoder
    encoder_inputs = Input(shape=(None,))
    x = Embedding(input_dim=num_encoder_tokens, output_dim=embedding_dim, mask_zero=True)(encoder_inputs)
    for _ in range(num_layers - 1):
        x = RNNLayer(hidden_units, return_sequences=True)(x)
    encoder_outputs, state_h, state_c = RNNLayer(hidden_units, return_state=True)(x)
    encoder_states = [state_h, state_c] if rnn_type == "LSTM" else [state_h]

    # Decoder
    decoder_inputs = Input(shape=(None,))
    x = Embedding(input_dim=num_decoder_tokens, output_dim=embedding_dim, mask_zero=True)(decoder_inputs)
    for _ in range(num_layers - 1):
        x = RNNLayer(hidden_units, return_sequences=True)(x, initial_state=encoder_states)
    if rnn_type == "LSTM":
        decoder_lstm, _, _ = RNNLayer(hidden_units, return_sequences=True, return_state=True)(x, initial_state=encoder_states)
    else:
        decoder_lstm = RNNLayer(hidden_units, return_sequences=True)(x, initial_state=encoder_states)
    decoder_dense = Dense(num_decoder_tokens, activation='softmax')
    decoder_outputs = decoder_dense(decoder_lstm)

    model = Model([encoder_inputs, decoder_inputs], decoder_outputs)
    model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    return model


In [4]:
# Example: Tokenizer for both encoder and decoder inputs
from tensorflow.keras.preprocessing.text import Tokenizer

# Assuming you have 'input_texts' for the source language (encoder) and 'output_texts' for the target language (decoder)
# input_texts and output_texts should be lists of sentences or sequences from your dataset
input_texts = ["hello", "world", "how", "are", "you"]
output_texts = ["hola", "mundo", "como", "estas", "tú"]

# Tokenizer for the encoder input data
encoder_tokenizer = Tokenizer()
encoder_tokenizer.fit_on_texts(input_texts)
num_encoder_tokens = len(encoder_tokenizer.word_index) + 1  # +1 for the padding token

# Tokenizer for the decoder output data
decoder_tokenizer = Tokenizer()
decoder_tokenizer.fit_on_texts(output_texts)
num_decoder_tokens = len(decoder_tokenizer.word_index) + 1  # +1 for the padding token

print(f"Number of encoder tokens: {num_encoder_tokens}")
print(f"Number of decoder tokens: {num_decoder_tokens}")


Number of encoder tokens: 6
Number of decoder tokens: 6


In [5]:
from tensorflow.keras.preprocessing.sequence import pad_sequences

# Convert input and output texts to sequences of integers
encoder_input_data = encoder_tokenizer.texts_to_sequences(input_texts)
decoder_input_data = decoder_tokenizer.texts_to_sequences(output_texts)

# Pad sequences to ensure they have the same length
max_encoder_seq_length = max([len(txt) for txt in encoder_input_data])
max_decoder_seq_length = max([len(txt) for txt in decoder_input_data])

encoder_input_data = pad_sequences(encoder_input_data, maxlen=max_encoder_seq_length, padding='post')
decoder_input_data = pad_sequences(decoder_input_data, maxlen=max_decoder_seq_length, padding='post')

print("Encoder Input Data Shape:", encoder_input_data.shape)
print("Decoder Input Data Shape:", decoder_input_data.shape)


Encoder Input Data Shape: (5, 1)
Decoder Input Data Shape: (5, 1)


In [6]:
import numpy as np

# One-hot encode the decoder output data
decoder_output_data = np.zeros(
    (len(output_texts), max_decoder_seq_length, num_decoder_tokens),
    dtype='float32'
)

for i, seq in enumerate(decoder_input_data):
    for t, token in enumerate(seq):
        decoder_output_data[i, t, token] = 1.0

print("Decoder Output Data Shape:", decoder_output_data.shape)


Decoder Output Data Shape: (5, 1, 6)


In [7]:
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, LSTM, Embedding, Dense

def create_seq2seq_model(rnn_type, embedding_dim, hidden_units, num_layers):
    # Encoder
    encoder_inputs = Input(shape=(None,))
    x = Embedding(input_dim=num_encoder_tokens, output_dim=embedding_dim, mask_zero=True)(encoder_inputs)

    for _ in range(num_layers - 1):
        x = rnn_type(hidden_units, return_sequences=True)(x)
    encoder_outputs, state_h, state_c = rnn_type(hidden_units, return_state=True)(x)

    # Decoder
    decoder_inputs = Input(shape=(None,))
    decoder_emb = Embedding(input_dim=num_decoder_tokens, output_dim=embedding_dim, mask_zero=True)(decoder_inputs)

    decoder_lstm = LSTM(hidden_units, return_sequences=True, return_state=True)
    decoder_outputs, _, _ = decoder_lstm(decoder_emb, initial_state=[state_h, state_c])

    decoder_dense = Dense(num_decoder_tokens, activation='softmax')
    decoder_outputs = decoder_dense(decoder_outputs)

    # Model
    model = Model([encoder_inputs, decoder_inputs], decoder_outputs)
    model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

    return model


In [8]:
# Define the model with the chosen configuration
model = create_seq2seq_model(rnn_type=LSTM, embedding_dim=128, hidden_units=256, num_layers=1)

# Train the model
model.fit([encoder_input_data, decoder_input_data], decoder_output_data,
          batch_size=64,
          epochs=2,  # Adjust the number of epochs based on your dataset
          validation_split=0.2)


Epoch 1/2
1/1 ━━━━━━━━━━━━━━━━━━━━ 6s 6s/step - accuracy: 0.2500 - loss: 1.7913 - val_accuracy: 0.0000e+00 - val_loss: 1.7946
Epoch 2/2
1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step - accuracy: 1.0000 - loss: 1.7707 - val_accuracy: 0.0000e+00 - val_loss: 1.8010
